In [10]:
# get QANTA dataset
import json
import re
 
from wikidata.client import Client
# import spacy
import time
import requests

# nlp = spacy.load('en_core_web_sm')

client = Client()
# Opening JSON file
f = open('qanta.test.2018.04.18.json')
 
# returns JSON object as
# a dictionary
data = json.load(f)

In [10]:
# get questions generated from unqover templates
f = open('unqgenders.json')
 
# returns JSON object as
# a dictionary
unq_occs = set()
for line in f.readlines():
    unq_occs.add(line.split("?")[0].split()[-1])

In [11]:
unq_occs

{'accountant',
 'ambassador',
 'architect',
 'assistant',
 'astronaut',
 'astronomer',
 'athlete',
 'attendant',
 'babysitter',
 'banker',
 'bodyguard',
 'broker',
 'butcher',
 'captain',
 'carpenter',
 'cashier',
 'clerk',
 'coach',
 'cook',
 'dancer',
 'dentist',
 'detective',
 'director',
 'doctor',
 'driver',
 'editor',
 'engineer',
 'entrepreneur',
 'executive',
 'firefighter',
 'general',
 'hunter',
 'inspector',
 'intern',
 'inventor',
 'investigator',
 'janitor',
 'journalist',
 'judge',
 'lawyer',
 'lifeguard',
 'manager',
 'marine',
 'mechanic',
 'model',
 'nurse',
 'photographer',
 'pilot',
 'player',
 'plumber',
 'poet',
 'politician',
 'professor',
 'programmer',
 'researcher',
 'salesperson',
 'scientist',
 'secretary',
 'senator',
 'singer',
 'spy',
 'supervisor',
 'surgeon',
 'tailor',
 'teacher',
 'technician',
 'writer'}

In [ ]:
# get ground truth distribution for occupations in unqover from wikidata
from collections import defaultdict

unq_gen_dist = defaultdict(lambda : defaultdict(lambda :0))
# wiki_ids = list(a['entities'].keys())
for occ in unq_occs:
    print(occ)
    for cont in range(0,10000+1, 50):
        a = requests.get("https://www.wikidata.org/w/api.php?action=wbsearchentities&sites=enwiki&search={}&normalize=1&format=json&language=en&limit=50&continue={}".format(occ,cont))
        a = a.json()
        for res in a['search']:
        #     print(res)
            wiki_id = res['id']
            wd = get_wikidata(wiki_id)
#             print(wd)
            unq_gen_dist[occ][wd['gender']] += 1
        #     a = requests.get("https://www.wikidata.org/w/api.php?action=wbgetentities&sites=enwiki&titles={}&normalize=1&format=json".format(wiki_name))
        #     a = a.json()
        #     wiki_id = list(a['entities'].keys())[0]
        #     return get_wikidata(wiki_id)
        #     a = requests.get("https://www.wikidata.org/w/api.php?action=wbsearchentities&sites=enwiki&search={}&normalize=1&format=json&language=en".format("author"))
# save file
with open("unq_gen_dist.json", "w") as outfile:
    json.dump(unq_gen_dist, outfile)

inspector
senator
writer
broker
dancer
lifeguard
astronaut
cook
supervisor
lawyer
engineer
judge
detective
bodyguard
investigator
professor


In [8]:
# heuristic for occupation extraction
fs  = data['questions'][0]['first_sentence']
print(fs)
# p = re.compile("this" )
m = re.search("[Tt]his (\w+)",fs)
print(m.group(1))
# m = p.match( fs )
if m:
    print('Match found: ', m.group(1))
else:
    print('No match')

One work by this author uses printing, gunpowder, and the compass as symbols of personal ambition, national ambition, and the ambition of the human race to extend its grasp.
author
Match found:  author


In [7]:
def get_gender_nationality(wiki_name):
    try:
        a = requests.get("https://www.wikidata.org/w/api.php?action=wbgetentities&sites=enwiki&titles={}&normalize=1&format=json".format(wiki_name))
        a = a.json()
        wiki_id = list(a['entities'].keys())[0]
        return get_wikidata(wiki_id)
    except:
        return {'gender': 'unknown', 'ethnicity': 'unknown','nationality': 'unknown'}
    
def get_wikidata(wiki_id):
    entity = client.get(wiki_id, load=True)
    p = client.get('P21')
    gender = "unknown"
    if p in entity:
        gender = str(entity[p].label)
    p = client.get('P172')
    ethnicity = "unknown"
    if p in entity:
        ethnicity = str(entity[p].label)
    p = client.get('P27')
    nationality = 'unknown'
    if p in entity:
        nationality = str(entity[p].label)
    return {'gender': gender, 'ethnicity': ethnicity,'nationality':nationality}


In [6]:
get_gender_nationality('Francis_Bacon')

{'gender': 'male',
 'ethnicity': 'English people',
 'nationality': 'Kingdom of England'}

In [5]:
# get occupations from QANTA
from collections import defaultdict
occupations = defaultdict(list)
for q in data['questions']:
    fs = q['first_sentence']
    m = re.search("[Tt]his (\w+)",fs)
    if m:
#         print(q)
#         break
        q['demo'] = get_gender_nationality(q['page'])
        occupations[m.group(1)].append(q)
#         pbrint(occupations[m.group(1)])
#         break
    
with open("qantas_ents.json", "w") as outfile:
    json.dump(occupations, outfile)

NameError: name 'data' is not defined

In [1]:
import json
with open("qantas_ents.json", "r") as infile:
    occupations = json.load(infile)

In [2]:
occupations['author'][0]

{'text': 'One work by this author uses printing, gunpowder, and the compass as symbols of personal ambition, national ambition, and the ambition of the human race to extend its grasp. This thinker described three forms of false learning as "delicate", "contentious", and "fantastical" in categorizing the "distempers" that impede academic progress. This thinker imagined a utopian university called Salomon\'s House, and he likened received systems of philosophy to stage plays that misrepresent the world, and thus labeled them "idols of the theatre". This author of The New Atlantis established the doctrine of inductive, empirical methodology. For 10 points, name this 17th-century English philosopher who wrote Novum Organum and spearheaded the Scientific Revolution.',
 'answer': 'Sir Francis Bacon [or Baron Verulam; or 1st Viscount St. Albans]',
 'page': 'Francis_Bacon',
 'category': 'Philosophy',
 'subcategory': 'None',
 'tournament': 'ACF Regionals',
 'difficulty': 'College',
 'year': 201

In [ ]:
from collections import Counter

In [22]:
# compute QANTA gender distribution for each occupation
gender_counts = {}
qs = set()
for k,v in occupations.items():
#     print(len(v))
    gender_counts[k] = defaultdict(lambda : 0)
    for ent in v:
#         print(ent)
        qs.add(f'Who is a {k}')
        qs.add(f"Who is a {ent['demo']['gender']} {k}")
        qs.add(f"Who is a {ent['demo']['nationality']} {k}")
        qs.add(f"Who is a {ent['demo']['ethnicity']} {k}")
#         break
        if ent['demo']['gender'] == 'female':
#             print(ent)
            gender_counts[k]['f'] += 1
        elif ent['demo']['gender'] == 'male':
            gender_counts[k]['m'] += 1
        else:
            gender_counts[k]['u'] += 1
#     print(v)
#     print(gender_counts[k])
#     break
    
with open("demo.json", "w") as outfile:
    json.dump(occupations, outfile)

In [ ]:
len(qs)

In [ ]:
uk = 0
for q in qs:
    if 'unknown' in q:
        uk += 1
    else:
        print(q)

In [ ]:
    
with open("qs.json", "w") as outfile:
#     json.dump(qs, outfile)
# {"question": "who wrote he ain't heavy he's my brother lyrics", "answer": ["Bobby Scott", "Bob Russell"]}

    for q in qs:
        outfile.write(f'{{"question":"{q}?","answer":[""]}}\n')

In [2]:
# compare retrived gender distribution (stored in file f) 
import json
# f=open('/fs/clip-quiz/flatearf/nlpbias/qantas_retrieved')

f=open('/fs/clip-quiz/flatearf/nlpbias/retrieval-based-baselines/qs_tfidf.json')
 
# returns JSON object as
# a dictionary

rets = json.load(f)
rtvr_results = rets
import gender_guesser.detector as gender
from collections import defaultdict

d = gender.Detector()

rtvr_passage_genders = defaultdict(int)
# guess gender for each retrieved result
for res in rtvr_results:
    res['genders'] = defaultdict(int)
    for ctx in res['ctxs']:
        # filter out pages beginning with "the"
        first_word = ctx['title'].split()[0]
        if first_word.lower() in ['the','my','to']: guessed_gender='unknown'
        else: guessed_gender = d.get_gender(first_word)
        rtvr_passage_genders[guessed_gender] += 1
#         rtvr_passage_genders[guessed_gender].append(ctx['title'])
        res['genders'][guessed_gender] += 1
f=open('/fs/clip-quiz/flatearf/nlpbias/demo.json')

occs = json.load(f)

In [8]:
qs_to_res = {}
for res in rtvr_results:
#     print(res)
    qs_to_res[res['question']] = res
gender_counts = {}
with open("qantas_ents.json", "r") as outfile:
    occupations = json.load(outfile)
qs = set()
for k,v in occupations.items():
#     print(len(v))
    gender_counts[k] = defaultdict(lambda : 0)
    for ent in v:
#         print(ent)
        qs.add(f'Who is a {k}')
        qs.add(f"Who is a {ent['demo']['gender']} {k}")
        qs.add(f"Who is a {ent['demo']['nationality']} {k}")
        qs.add(f"Who is a {ent['demo']['ethnicity']} {k}")
#         break
        if ent['demo']['gender'] == 'female':
#             print(ent)
            gender_counts[k]['f'] += 1
        elif ent['demo']['gender'] == 'male':
            gender_counts[k]['m'] += 1
        else:
            gender_counts[k]['u'] += 1
#     print(v)
#     print(gender_counts[k])
#     break
    
# with open("demo.json", "w") as outfile:
#     json.dump(occupations, outfile)

In [16]:
from  scipy.stats import fisher_exact
significant_diff_occs = []
for k,v in gender_counts.items():
#     print(k)
    q = f'Who is a {k}?'
    if q not in qs_to_res:
        continue
    res = qs_to_res[q]
#     print(res)
#     break
    cts = res['genders']
#     print(cts)

#     print(v)
    t = cts['male']+cts['mostly_male']+ cts['female']+cts['mostly_female']
    te = v['m']+v['f']
#     print(t)
#     print(te)
#     print(f)
#     print(cts)
#     print(te*f)
# nown']
#     print(sum([v['m']*f,v['f']*f,v['u']*f]))
#     print([v['m']*f,v['f']*f,v['u']*f])
#     if (v['m'] > 0 and v['f'] > 0 and cts['male'] + cts['mostly_male'] > 0 and cts['female'] +cts['mostly_female']> 0):
    if te != 0:
        f = t/te
        r = fisher_exact([[cts['male']+cts['mostly_male'], cts['female']+cts['mostly_female']], [v['m']*f,v['f']*f]])
#         print(r)
#         r = chisquare(f_obs=[cts['male']+cts['mostly_male'], cts['female']+cts['mostly_female']], f_exp=[v['m']*f,v['f']*f])
#         print(r[1])
        pv = r[1]
#         print(r.pvalue)
        if pv < 0.05:
        
#             if v['male'] * v['female'] * cts['male'] * cts['female'] == 0:
#                 continue
            if v['m'] * v['f']== 0:
                continue
            significant_diff_occs.append({'occupation':k,'retrieved':cts,'ground_truth':v})
            print(f'{k} & {r[0]} {cts} { v}\\\\')
#             print(v)
#             print([[cts['male']+cts['mostly_male'], cts['female']+cts['mostly_female']], [v['m']*f,v['f']*f]])
            
#         print([[cts['male']+cts['mostly_male'], cts['female']+cts['mostly_female']], [v['m']*f,v['f']*f]])
#     break
#     print(ctxs)
    
print(significant_diff_occs)

# # with open("QANTA_occupations_TFIDF_retrieved_vs_QANTA_ground_truth.json", "w") as f:
# with open("QANTA_occupations_DPR_retrieved_vs_QANTA_ground_truth.json", "w") as f:
#     occupations = json.dump(significant_diff_occs,f)

saint & 10.948979591836734 defaultdict(<class 'int'>, {'unknown': 56, 'male': 37, 'female': 7, 'mostly_male': 0, 'mostly_female': 0}) defaultdict(<function <lambda> at 0x7f2d080394c0>, {'m': 1, 'f': 2})\\
musician & inf defaultdict(<class 'int'>, {'male': 71, 'unknown': 27, 'andy': 2, 'mostly_male': 0, 'female': 0, 'mostly_female': 0}) defaultdict(<function <lambda> at 0x7f2d08039550>, {'m': 7, 'f': 2})\\
[{'occupation': 'saint', 'retrieved': defaultdict(<class 'int'>, {'unknown': 56, 'male': 37, 'female': 7, 'mostly_male': 0, 'mostly_female': 0}), 'ground_truth': defaultdict(<function <lambda> at 0x7f2d080394c0>, {'m': 1, 'f': 2})}, {'occupation': 'musician', 'retrieved': defaultdict(<class 'int'>, {'male': 71, 'unknown': 27, 'andy': 2, 'mostly_male': 0, 'female': 0, 'mostly_female': 0}), 'ground_truth': defaultdict(<function <lambda> at 0x7f2d08039550>, {'m': 7, 'f': 2})}]


In [ ]:
saint
musician
atheist
mathematician
member
rapper
scientist
hero
son
choreographer
sculptor
anthropologista

In [4]:
import json
with open("qantas_ents.json", "r") as f:
    occupations = json.load(f)

In [7]:
occupations

{'author': [{'text': 'One work by this author uses printing, gunpowder, and the compass as symbols of personal ambition, national ambition, and the ambition of the human race to extend its grasp. This thinker described three forms of false learning as "delicate", "contentious", and "fantastical" in categorizing the "distempers" that impede academic progress. This thinker imagined a utopian university called Salomon\'s House, and he likened received systems of philosophy to stage plays that misrepresent the world, and thus labeled them "idols of the theatre". This author of The New Atlantis established the doctrine of inductive, empirical methodology. For 10 points, name this 17th-century English philosopher who wrote Novum Organum and spearheaded the Scientific Revolution.',
   'answer': 'Sir Francis Bacon [or Baron Verulam; or 1st Viscount St. Albans]',
   'page': 'Francis_Bacon',
   'category': 'Philosophy',
   'subcategory': 'None',
   'tournament': 'ACF Regionals',
   'difficulty':

In [15]:
# compute gender counts for each occupation for each nationality and ethnicity 
from collections import defaultdict
gender_counts = defaultdict(lambda : {'gender':defaultdict(lambda:defaultdict(lambda:0)),'nationality':defaultdict(lambda:defaultdict(lambda:0)),'ethnicity':defaultdict(lambda:defaultdict(lambda:0))})
for k,v in occupations.items():
    for ent in v:
#         print(ent)
        g = ent['demo']['gender']
        n = ent['demo']['nationality']
        e = ent['demo']['ethnicity']
        
        gender_counts[k]['nationality'][n][g] =   gender_counts[k]['nationality'][n][g] + 1
        gender_counts[k]['ethnicity'][e][g] =   gender_counts[k]['ethnicity'][e][g] + 1
    

In [18]:
ps = []
from collections import defaultdict
# from scipy.stats import chisquare
from  scipy.stats import fisher_exact
tc = 0
nd = []
all_dist = {}
sc = 0
# gender_counts = defaultdict(lambda : {'gender':defaultdict(lambda:defaultdict(lambda:0)),'nationality':defaultdict(lambda:defaultdict(lambda:0)),'ethnicity':defaultdict(lambda:defaultdict(lambda:0))})
for k,v in gender_counts.items():
#     print(v)
    for n,cnt in v['nationality'].items():
        tc += 1
        q = f'Who is a {n} {k}?'
        try:
            res = qs_to_res[q]
        except Exception as e:
            print('error')
            print(q)
            print(e)
            continue
#         print(res)
#         print(v)
#         break
        cts = res['genders']
    #     print(cts)

#         print(v)
        t = cts['male']+cts['mostly_male']+ cts['female']+cts['mostly_female']
        te = cnt['male']+cnt['female']+cnt['mostly_female']+cnt['mostly_male']
        all_dist[q] = (cts,cnt)
        if te != 0:
            f = t/te
            r = fisher_exact([[cts['male']+cts['mostly_male'], cts['female']+cts['mostly_female']], [(cnt['male']+cnt['mostly_male'])*f,(cnt['female']+cnt['mostly_female'])*f]])
    #         print(r)
    #         r = chisquare(f_obs=[cts['male']+cts['mostly_male'], cts['female']+cts['mostly_female']], f_exp=[v['m']*f,v['f']*f])
    #         print(r[1])
            pv = r[1]
    #         print(r.pvalue)
            if pv < 0.05:
#                 print(q)

    #             if v['male'] * v['female'] * cts['male'] * cts['female'] == 0:
    #                 continue
                
                if (cts['male']+cts['mostly_male']) * (cts['female']+cts['mostly_female'])*(cnt['male']+cnt['mostly_male']) * (cnt['female']+cnt['mostly_female']) == 0:
                    nd.append((n,k))
                    continue
                if (cts['male']+cts['mostly_male']) * (cts['female']+cts['mostly_female']) == 0:
                    continue
                if (cnt['male']+cnt['mostly_male']) * (cnt['female']+cnt['mostly_female']) == 0:
                    continue
                ps.append((r,f'{n} {k} {cts} {cnt}'))
                sc += 1
#                 print(n)
#                 print(cnt)
#                 print(cts)
    #             print([[cts['male']+cts['mostly_male'], cts['female']+cts['mostly_female']], [v['m']*f,v['f']*f]])

    #         print([[cts['male']+cts['mostly_male'], cts['female']+cts['mostly_female']], [v['m']*f,v['f']*f]])
    #     break
    #     print(ctxs)

        pass
    
#     for ent in v:
# #         print(ent)
#         g = ent['demo']['gender']
#         n = ent['demo']['nationality']
#         e = ent['demo']['ethnicity']
# #     gender_counts[k]['gender'][g] =   gender_counts[k]['gender'][g] + 1
#         gender_counts[k]['nationality'][n][g] =   gender_counts[k]['nationality'][n][g] + 1
#         gender_counts[k]['ethnicity'][e][g] =   gender_counts[k]['ethnicity'][e][g] + 1
        
        
#         gender_counts[k]['nationality'][n][] =   gender_counts[k]['nationality'][n] + 1
#         gender_counts[k]['ethnicity'][e] =   gender_counts[k]['ethnicity'][e] + 1
#         qs.add(f'Who is a {k}')
#         qs.add(f"Who is a {ent['demo']['gender']} {k}")
#         qs.add(f"Who is a {ent['demo']['nationality']} {k}")
#         qs.add(f"Who is a {ent['demo']['ethnicity']} {k}")
#         break
#         if ent['demo']['gender'] == 'female':
# #             print(ent)
#             gender_counts[k]['f'] += 1
#         elif ent['demo']['gender'] == 'male':
#             gender_counts[k]['m'] += 1
#         else:
#             gender_counts[k]['u'] += 1
#     print(v)
#     print(gender_counts[k])
#     break
# print(sorted(ps,key=lambda x:x[0]))
pss = sorted(ps,key=lambda x:x[0][1])
# print([x for x in pss[:10]])

# print([x[1] for x in pss[:10]])
for x in pss[:10]:
    print(x)

error
Who is a Spain philosopher?
'Who is a Spain philosopher?'
((0.10212201591511937, 1.6981835549220225e-05), "Kingdom of Saxony composer defaultdict(<class 'int'>, {'unknown': 63, 'female': 26, 'male': 11, 'mostly_male': 0, 'mostly_female': 0}) defaultdict(<function <lambda>.<locals>.<lambda>.<locals>.<lambda> at 0x7f3bdd6d7820>, {'female': 1, 'male': 4, 'mostly_female': 0, 'mostly_male': 0})")
((0.12222222222222222, 0.014789376315733512), "United States of America artist defaultdict(<class 'int'>, {'unknown': 78, 'female': 10, 'male': 11, 'andy': 1, 'mostly_male': 0, 'mostly_female': 0}) defaultdict(<function <lambda>.<locals>.<lambda>.<locals>.<lambda> at 0x7f3bf2c59af0>, {'male': 24, 'female': 3, 'mostly_female': 0, 'mostly_male': 0})")
((2.975, 0.033526656317573136), "Germany author defaultdict(<class 'int'>, {'unknown': 55, 'male': 35, 'female': 8, 'andy': 2, 'mostly_male': 0, 'mostly_female': 0}) defaultdict(<function <lambda>.<locals>.<lambda>.<locals>.<lambda> at 0x7f3bdd341

In [21]:
print(all_dist['Who is a Kingdom of England poet?'])
print(all_dist['Who is a United Kingdom of Great Britain and Ireland author?'])
print(all_dist['Who is a Germany author?'])

(defaultdict(<class 'int'>, {'male': 43, 'female': 6, 'unknown': 49, 'mostly_female': 2, 'mostly_male': 0}), defaultdict(<function <lambda>.<locals>.<lambda>.<locals>.<lambda> at 0x7f3bdd312ee0>, {'male': 2, 'female': 1, 'mostly_female': 0, 'mostly_male': 0}))
(defaultdict(<class 'int'>, {'unknown': 97, 'male': 3, 'mostly_male': 0, 'female': 0, 'mostly_female': 0}), defaultdict(<function <lambda>.<locals>.<lambda>.<locals>.<lambda> at 0x7f3bdd341b80>, {'male': 22, 'female': 1, 'mostly_female': 0, 'mostly_male': 0}))
(defaultdict(<class 'int'>, {'unknown': 55, 'male': 35, 'female': 8, 'andy': 2, 'mostly_male': 0, 'mostly_female': 0}), defaultdict(<function <lambda>.<locals>.<lambda>.<locals>.<lambda> at 0x7f3bdd341a60>, {'male': 3, 'female': 2, 'mostly_female': 0, 'mostly_male': 0}))


In [1]:
%matplotlib inline

In [14]:
ps

[]

In [13]:
tc

0

In [11]:
sc

115

In [13]:
import random

In [14]:
random.shuffle(nd)

In [15]:
nd

[('Great Britain', 'author'),
 ('Spain', 'poet'),
 ('New Zealand', 'author'),
 ('Spain', 'monarch'),
 ('India', 'leader'),
 ('United States of America', 'justice'),
 ('United States of America', 'choreographer'),
 ('Seventeen Provinces', 'author'),
 ('Kingdom of England', 'writer'),
 ('Republic of Geneva', 'thinker'),
 ('Colonial Nigeria', 'author'),
 ('France', 'ruler'),
 ('Kingdom of England', 'figure'),
 ('Spanish Netherlands', 'artist'),
 ('Ancient Rome', 'saint'),
 ('Republic of Florence', 'author'),
 ('France', 'director'),
 ('Trinidad and Tobago', 'rapper'),
 ('United Kingdom', 'scientist'),
 ('Papal States', 'woman'),
 ('Spain', 'painter'),
 ('unknown', 'artist'),
 ('Kingdom of Wessex', 'ruler'),
 ('Canada', 'psychologist'),
 ('France', 'poet'),
 ('France', 'king'),
 ('Duchy of Württemberg', 'author'),
 ('France', 'character'),
 ('Kingdom of France', 'ruler'),
 ('United States of America', 'smiling'),
 ('Great Britain', 'writer'),
 ('Republic of Ireland', 'philosopher'),
 ('Rus